## STRATEGY 

Parameters:
	Stretch:	0.5
	LongTermMALen:	200
	ShortTermMALen:	20
		
Data:
	ATRValue:	ATR(3)
	ADXValue:	ADX(5)
	
	ShortTermMA:	MA(Close, ShortTermMALen)
	LongTermMA:	MA(Close, LongTermMALen)

	ClosingRange:	(Close - Low) / (High - Low)
	IsUptrend: 	Close > LongTermMA
	IsVolatile:	ADXValue > 30			  

	Long_limit:	    Low - (ATRValue * Stretch) // limit order price
	Long_trigger:	ClosingRange < 0.3 // close in lower 30% of bar
	Long_setup:	    LongTrigger and IsUptrend and IsLiquid and IsVolatile
	
	StopLossExit:	Close < ShortTermMA



	Exit_rule:	Close > FillPrice or StopLossExit
	Exit_price:	NextOpen

1. go through and simplify or explain with comments
1b. try to use pairname to access data for better readability
2. use try to create object (not to long)
3. start process from beginning to see how repeadble it is 

In [91]:
import vectorbt as vbt
import pandas as pd 
import numpy as np
from datetime import datetime
from kucoin_candle_spot import SpotDataFetcher
from datetime import datetime, timezone
import pandas_ta as ta
from numba import njit
import plotly.graph_objs as go


## data collection

In [92]:

symbols = ["ETH-USDT", "BTC-USDT","XRP-USDT","SOL-USDT"]
timeframe = "4hour"
start_time = "2018-01-08 10:00:00"
end_time = datetime.now(timezone.utc).strftime("%Y-%m-%d %H:%M:%S")


# Fetch data for each symbol and store in a dictionary
dataframes = {}
for symbol in symbols:
    fetcher = SpotDataFetcher(symbol, timeframe, start_time, end_time)
    df = fetcher.fetch_candles_as_df()
    df['symbol'] = symbol
    dataframes[symbol] = df

# Print the DataFrame for each symbol
for symbol, df in dataframes.items():
    print(f"\nDataFrame for {symbol}:")
    print(df)
# fetcher = SpotDataFetcher(symbol, timeframe, start_time, end_time)




INFO:kucoin_candle_spot.kucoin_fetch_spot:Fetching candle data...
INFO:kucoin_candle_spot.kucoin_fetch_spot:Fetch complete. Chunks: 12, Candles: 15476
INFO:kucoin_candle_spot.kucoin_fetch_spot:Fetching candle data...
INFO:kucoin_candle_spot.kucoin_fetch_spot:Fetch complete. Chunks: 12, Candles: 15476
INFO:kucoin_candle_spot.kucoin_fetch_spot:Fetching candle data...
INFO:kucoin_candle_spot.kucoin_fetch_spot:Fetch complete. Chunks: 10, Candles: 13229
INFO:kucoin_candle_spot.kucoin_fetch_spot:Fetching candle data...
INFO:kucoin_candle_spot.kucoin_fetch_spot:Fetch complete. Chunks: 7, Candles: 7653



DataFrame for ETH-USDT:
                                  open        close         high         low  \
timestamp                                                                      
2018-01-08 12:00:00+00:00  1150.000000  1026.111430  1195.000000   910.00000   
2018-01-08 16:00:00+00:00  1026.111430  1144.000000  1144.999999  1026.11143   
2018-01-08 20:00:00+00:00  1144.000000  1165.832998  1187.999998  1102.00000   
2018-01-09 00:00:00+00:00  1135.000000  1203.000004  1229.999969  1123.56120   
2018-01-09 04:00:00+00:00  1203.000004  1195.000000  1250.225623  1176.00000   
...                                ...          ...          ...         ...   
2025-01-30 00:00:00+00:00  3114.050000  3202.030000  3202.770000  3091.62000   
2025-01-30 04:00:00+00:00  3201.580000  3190.550000  3215.610000  3178.52000   
2025-01-30 08:00:00+00:00  3190.550000  3222.330000  3229.450000  3181.41000   
2025-01-30 12:00:00+00:00  3222.340000  3255.220000  3280.830000  3209.20000   
2025-01-30 16:0

In [93]:
df_eth = dataframes['ETH-USDT']
df_btc = dataframes['BTC-USDT']
df_btc

open          close           high  \
timestamp                                                                
2018-01-08 12:00:00+00:00   15258.070771   13906.174267   15500.000000   
2018-01-08 16:00:00+00:00   13619.578000   15200.000000   15499.000000   
2018-01-08 20:00:00+00:00   15100.000000   15091.910250   15499.000000   
2018-01-09 00:00:00+00:00   15077.718600   15230.000000   15850.000000   
2018-01-09 04:00:00+00:00   15230.000000   14989.990000   15799.669768   
...                                  ...            ...            ...   
2025-01-30 00:00:00+00:00  103742.000000  105209.300000  105306.800000   
2025-01-30 04:00:00+00:00  105196.600000  105121.300000  105598.900000   
2025-01-30 08:00:00+00:00  105128.800000  105288.800000  105539.200000   
2025-01-30 12:00:00+00:00  105288.800000  105560.300000  106447.300000   
2025-01-30 16:00:00+00:00  105560.300000  105046.400000  106000.000000   

                                     low                volume  \
timestamp                                                        
2018-01-08 12:00:00+00:00   12001.000000          108.60920029   
2018-01-08 16:00:00+00:00   13619.578000           60.51195804   
2018-01-08 20:00:00+00:00   14499.800000            26.0352418   
2018-01-09 00:00:00+00:00   14858.277611           22.59635092   
2018-01-09 04:00:00+00:00   14535.000000           28.99277165   
...                                  ...                   ...   
2025-01-30 00:00:00+00:00  103266.600000          328.32632316   
2025-01-30 04:00:00+00:00  104800.700000          252.29068234   
2025-01-30 08:00:00+00:00  104916.500000          173.41997171   
2025-01-30 12:00:00+00:00  104665.300000  503.4096081509134158   
2025-01-30 16:00:00+00:00  104917.000000    202.05845958108822   

                                             turnover    symbol  
timestamp                                                        
2018-01-08 12:00:00+00:00            1504244.57615939  BTC-USDT  
2018-01-08 16:00:00+00:00             871383.04922384  BTC-USDT  
2018-01-08 20:00:00+00:00             387149.14421422  BTC-USDT  
2018-01-09 00:00:00+00:00             342880.23918465  BTC-USDT  
2018-01-09 04:00:00+00:00             438004.24371563  BTC-USDT  
...                                               ...       ...  
2025-01-30 00:00:00+00:00          34209748.013166129  BTC-USDT  
2025-01-30 04:00:00+00:00          26542614.494908484  BTC-USDT  
2025-01-30 08:00:00+00:00          18248479.983540628  BTC-USDT  
2025-01-30 12:00:00+00:00  53142922.55010213230135243  BTC-USDT  
2025-01-30 16:00:00+00:00   21300414.4516970204304492  BTC-USDT  

[15476 rows x 7 columns]

In [94]:
def custom_trading_strategy(close, high, low, stretch=0.5, 
                             long_term_ma_len=200, short_term_ma_len=20, adx_len=5, atr_len=3, symbol=None):
    # Calculate indicators
    atr = vbt.IndicatorFactory.from_talib('ATR').run(high, low, close, timeperiod=atr_len).real.to_numpy()
    adx = vbt.IndicatorFactory.from_talib('ADX').run(high, low, close, timeperiod=adx_len).real.to_numpy()
    
    # Moving Averages
    long_term_ma = vbt.IndicatorFactory.from_talib('EMA').run(close, timeperiod=long_term_ma_len).real.to_numpy()
    short_term_ma = vbt.IndicatorFactory.from_talib('EMA').run(close, timeperiod=short_term_ma_len).real.to_numpy()

    # Closing Range
    closing_range = (close - low) / (high - low)
    
    # Conditions
    is_uptrend = close > long_term_ma
    is_volatile = adx > 30
    
    # Long Limit
    long_limit = low - (atr * stretch)
    
    # Long Trigger
    long_trigger = closing_range < 0.3
    
    # Long Setup
    long_setup = long_trigger & is_uptrend & is_volatile
    
    # Return limit order price when conditions for long setup are met
    limit_order_price = np.where(long_setup, long_limit, np.nan)
    
    # Ensure the order of outputs matches output_names
    return limit_order_price, long_term_ma,short_term_ma, atr, adx

# Create the indicator factory
custom_strategy_indicator = vbt.IndicatorFactory(
    class_name='CustomTradingStrategy',
    short_name='custom_strategy',
    input_names=['Close', 'High', 'Low'],
    param_names=['stretch', 'long_term_ma_len','short_term_ma_len', 'adx_len', 'atr_len','symbol'],
    output_names=['limit_order_price' ,'long_term_ma','short_term_ma', 'atr', 'adx']  # Add outputs for indicators

).from_apply_func(custom_trading_strategy)




In [95]:
# Entry parameter 
stretch = 0.5
long_term_ma_len = [100,200]
adx_len = [5,6]
atr_len = 3

# exit parameter
short_term_ma_len = [20,30,40]

check_df = []
indiactor_obj = []
for symbol in symbols:
    print(symbol)
    df = dataframes[symbol]
    check_df.append(df)
    # Usage example (commented out)
    indicator = custom_strategy_indicator.run(
        df['close'], df['high'], df['low'],
        stretch=stretch,
        long_term_ma_len=long_term_ma_len,
        short_term_ma_len=short_term_ma_len,
        adx_len=adx_len,
        atr_len=atr_len,
        symbol=symbol,
        param_product=True

    )
    indiactor_obj.append(indicator)

# df_indicator_signals = indicator.limit_order_price
# df_indicator_signals




ETH-USDT


/var/folders/33/gyg8_bbj4qn5_tvszhbzjxdm0000gn/T/ipykernel_94930/1916122639.py:12: RuntimeWarning:

invalid value encountered in divide



BTC-USDT


/var/folders/33/gyg8_bbj4qn5_tvszhbzjxdm0000gn/T/ipykernel_94930/1916122639.py:12: RuntimeWarning:

invalid value encountered in divide



XRP-USDT


/var/folders/33/gyg8_bbj4qn5_tvszhbzjxdm0000gn/T/ipykernel_94930/1916122639.py:12: RuntimeWarning:

invalid value encountered in divide



SOL-USDT


In [96]:
check_df[3]

open    close     high      low          volume  \
timestamp                                                                       
2021-08-04 08:00:00+00:00   25.000   34.314   50.000   25.000   6010.20940332   
2021-08-04 12:00:00+00:00   34.393   35.456   35.706   34.393   5592.77378218   
2021-08-04 16:00:00+00:00   35.315   36.238   36.530   35.242   4894.80479095   
2021-08-04 20:00:00+00:00   36.238   35.799   36.684   35.722    3486.3455887   
2021-08-05 00:00:00+00:00   35.720   37.350   37.457   35.580   4473.56802142   
...                            ...      ...      ...      ...             ...   
2025-01-30 00:00:00+00:00  228.156  240.278  241.034  226.858  97683.86391728   
2025-01-30 04:00:00+00:00  240.227  238.915  242.013  237.208  61590.72729743   
2025-01-30 08:00:00+00:00  238.890  241.770  241.852  238.048  58522.26829264   
2025-01-30 12:00:00+00:00  241.827  241.053  244.657  239.113  74379.91179959   
2025-01-30 16:00:00+00:00  241.119  240.296  243.374  240.037  37981.93642684   

                                       turnover    symbol  
timestamp                                                  
2021-08-04 08:00:00+00:00    204117.54565327886  SOL-USDT  
2021-08-04 12:00:00+00:00     195584.8785090125  SOL-USDT  
2021-08-04 16:00:00+00:00    175493.95726710482  SOL-USDT  
2021-08-04 20:00:00+00:00    126602.82652431746  SOL-USDT  
2021-08-05 00:00:00+00:00    162502.87463391611  SOL-USDT  
...                                         ...       ...  
2025-01-30 00:00:00+00:00  22896664.61471645015  SOL-USDT  
2025-01-30 04:00:00+00:00  14774698.30777771861  SOL-USDT  
2025-01-30 08:00:00+00:00  14060973.15190647545  SOL-USDT  
2025-01-30 12:00:00+00:00   17936800.8278205032  SOL-USDT  
2025-01-30 16:00:00+00:00   9183063.94865578538  SOL-USDT  

[7653 rows x 7 columns]

In [97]:
def copy_rename_close_series(df_original, df_indicator_signals):

    def repeat_series_horizontally(series, target_shape):
        return np.tile(series.values.reshape(-1, 1), target_shape[1])

    # Assuming df and df_indicator_signals are already defined
    nedded_copies = len(df_indicator_signals.columns)

    # Repeat the 'close' series horizontally to match the shape of df_indicator_signals
    df_dublicate_close = pd.DataFrame(repeat_series_horizontally(df_original['close'], df_indicator_signals.shape), index=df_original.index)

    # Rename columns if shapes match
    if df_indicator_signals.shape == df_dublicate_close.shape:
        df_dublicate_close.columns = df_indicator_signals.columns
        print("Columns have been renamed")
    else:
        print("The DataFrames do not have the same shape.")
    
    
    return df_dublicate_close

# how to access the columns ----> e.g. df_dublicate_close[(0.5, 100, 20, 5, 3,'BTC-USDT')]
df_dublicate_close_pairs =[]
for symbol_position in range(len(indiactor_obj)):
    df = check_df[symbol_position]
    df_dublicate_close = copy_rename_close_series(df, indiactor_obj[symbol_position].limit_order_price)
    df_dublicate_close_pairs.append(df_dublicate_close)




Columns have been renamed
Columns have been renamed
Columns have been renamed
Columns have been renamed


In [98]:
df_dublicate_close_pairs

[custom_strategy_stretch                    0.5                            \
 custom_strategy_long_term_ma_len           100                             
 custom_strategy_short_term_ma_len           20                        30   
 custom_strategy_adx_len                      5            6            5   
 custom_strategy_atr_len                      3            3            3   
 custom_strategy_symbol                ETH-USDT     ETH-USDT     ETH-USDT   
 timestamp                                                                  
 2018-01-08 12:00:00+00:00          1026.111430  1026.111430  1026.111430   
 2018-01-08 16:00:00+00:00          1144.000000  1144.000000  1144.000000   
 2018-01-08 20:00:00+00:00          1165.832998  1165.832998  1165.832998   
 2018-01-09 00:00:00+00:00          1203.000004  1203.000004  1203.000004   
 2018-01-09 04:00:00+00:00          1195.000000  1195.000000  1195.000000   
 ...                                        ...          ...          ...   

In [99]:
import numpy as np
import vectorbt as vbt
from numba import njit
import talib
from vectorbt.portfolio.enums import SizeType, Direction

# Create arrays to store the data we want to plot
@njit
def order_func_nb(c, high, low, open_, entries, ma_short, entry_price):  # Added entry_price parameter
    close_price = c.close[c.i, c.col]
    close_minus_1bar = c.close[c.i-1, c.col]
    
    # if in position 
    if c.position_now > 0:
        if (close_minus_1bar <= ma_short[c.i-1]) or (close_price > entry_price[c.i]):
            value = vbt.portfolio.nb.order_nb(
                size=-np.inf,
                price=open_[c.i],
                size_type=SizeType.Amount,
                direction=Direction.LongOnly,
                fees=0.001,
                slippage=0.002)
            # Store exit data
            return value

    # if not in position search for position to enter
    elif (c.position_now == 0) and (c.i != 0):
        if (entries[c.i-1,c.col] > 0) and (low[c.i] < entries[c.i-1,c.col]):
            entry_price[:] = np.nan  # Reset entry price array
            entry_price[:] = entries[c.i-1,c.col]  # Update entry price array

            order = vbt.portfolio.nb.order_nb(
                size=1,
                price=entry_price[c.i],
                size_type=SizeType.Percent,
                direction=Direction.LongOnly,
                fees=0.001,
                slippage=0.002,
                allow_partial=False,
                raise_reject=True
            )
            return order

    return vbt.portfolio.enums.NoOrder



In [100]:
pf_pairs = []    

for symbol, symbol_position in zip(symbols, range(len(symbols))):
    # candle data
    close = df_dublicate_close_pairs[symbol_position]
    print(close)
    open_ =dataframes[symbol]['open'].to_numpy().flatten()
    high = dataframes[symbol]['high'].to_numpy().flatten()
    low = dataframes[symbol]['low'].to_numpy().flatten()
    # high = df['high'].to_numpy().flatten()
    # low = df['low'].to_numpy().flatten()

    # indicator data
    entries = indiactor_obj[symbol_position].limit_order_price.to_numpy()
    # entries = df_indicator_signals.to_numpy()
    ma_short = indiactor_obj[symbol_position].short_term_ma.to_numpy().flatten()
    # ma_short = indicator.short_term_ma.to_numpy().flatten()

    # Create arrays to store data
    entry_price = np.full(close.shape[0], np.nan)  # Initialize entry price array

    # Create portfolio with trade_data
    pf = vbt.Portfolio.from_order_func(
        close,
        order_func_nb,
        high,
        low,
        open_,
        entries,
        ma_short,
        entry_price,  # Pass entry_price array to the function
        init_cash=500
    )

    pf_pairs.append(pf)



custom_strategy_stretch                    0.5                            \
custom_strategy_long_term_ma_len           100                             
custom_strategy_short_term_ma_len           20                        30   
custom_strategy_adx_len                      5            6            5   
custom_strategy_atr_len                      3            3            3   
custom_strategy_symbol                ETH-USDT     ETH-USDT     ETH-USDT   
timestamp                                                                  
2018-01-08 12:00:00+00:00          1026.111430  1026.111430  1026.111430   
2018-01-08 16:00:00+00:00          1144.000000  1144.000000  1144.000000   
2018-01-08 20:00:00+00:00          1165.832998  1165.832998  1165.832998   
2018-01-09 00:00:00+00:00          1203.000004  1203.000004  1203.000004   
2018-01-09 04:00:00+00:00          1195.000000  1195.000000  1195.000000   
...                                        ...          ...          ...   
2025-01-30 0

In [101]:
test= pf_pairs[1][(0.5,                      100,                               20,                                 5,                        3,'BTC-USDT')]
test.plot().show()  

In [102]:
# return_and_maxdd_list = []
# for pf in pf_pairs:
#     total_return = pf.total_return()
#     max_dd = pf.max_drawdown()
#     total_return
#     return_and_maxdd = pd.concat([total_return, max_dd], axis=1)
#     return_and_maxdd_list.append(return_and_maxdd)




# Assuming return_and_maxdd_list is a list of DataFrames
return_and_maxdd_list = []
for pf in pf_pairs:
    total_return = pf.total_return()
    max_dd = pf.max_drawdown()
    return_and_maxdd = pd.concat([total_return, max_dd], axis=1)
    return_and_maxdd_list.append(return_and_maxdd)

# Concatenate all DataFrames along the rows
combined_df = pd.concat(return_and_maxdd_list, axis=0)

combined_df



total_return  \
custom_strategy_stretch custom_strategy_long_term_ma_len custom_strategy_short_term_ma_len custom_strategy_adx_len custom_strategy_atr_len custom_strategy_symbol                 
0.5                     100                              20                                5                       3                       ETH-USDT                   -0.608810   
                                                                                           6                       3                       ETH-USDT                   -0.550108   
                                                         30                                5                       3                       ETH-USDT                   -0.608810   
                                                                                           6                       3                       ETH-USDT                   -0.550108   
                                                         40                                5                       3                       ETH-USDT                   -0.608810   
                                                                                           6                       3                       ETH-USDT                   -0.550108   
                        200                              20                                5                       3                       ETH-USDT                   -0.622586   
                                                                                           6                       3                       ETH-USDT                   -0.559609   
                                                         30                                5                       3                       ETH-USDT                   -0.622586   
                                                                                           6                       3                       ETH-USDT                   -0.559609   
                                                         40                                5                       3                       ETH-USDT                   -0.622586   
                                                                                           6                       3                       ETH-USDT                   -0.559609   
                        100                              20                                5                       3                       BTC-USDT                   -0.573489   
                                                                                           6                       3                       BTC-USDT                   -0.564952   
                                                         30                                5                       3                       BTC-USDT                   -0.573489   
                                                                                           6                       3                       BTC-USDT                   -0.564952   
                                                         40                                5                       3                       BTC-USDT                   -0.573489   
                                                                                           6                       3                       BTC-USDT                   -0.564952   
                        200                              20                                5                       3                       BTC-USDT                   -0.627593   
                                                                                           6                       3                       BTC-USDT                   -0.661849   
                                                         30                                5                       3                       BTC-USDT                   -0.627593   
                                              

In [103]:
total_return = pf.total_return()
max_dd = pf.max_drawdown()
total_return
return_and_maxdd = pd.concat([total_return, max_dd], axis=1)
return_and_maxdd.sort_values(by='total_return', ascending=False).head(50)

total_return  \
custom_strategy_stretch custom_strategy_long_term_ma_len custom_strategy_short_term_ma_len custom_strategy_adx_len custom_strategy_atr_len custom_strategy_symbol                 
0.5                     200                              20                                6                       3                       SOL-USDT                   -0.812157   
                                                         30                                6                       3                       SOL-USDT                   -0.812157   
                                                         40                                6                       3                       SOL-USDT                   -0.812157   
                        100                              20                                6                       3                       SOL-USDT                   -0.815515   
                                                         30                                6                       3                       SOL-USDT                   -0.815515   
                                                         40                                6                       3                       SOL-USDT                   -0.815515   
                        200                              20                                5                       3                       SOL-USDT                   -0.824729   
                                                         30                                5                       3                       SOL-USDT                   -0.824729   
                                                         40                                5                       3                       SOL-USDT                   -0.824729   
                        100                              20                                5                       3                       SOL-USDT                   -0.832598   
                                                         30                                5                       3                       SOL-USDT                   -0.832598   
                                                         40                                5                       3                       SOL-USDT                   -0.832598   

                                                                                                                                                                   max_drawdown  
custom_strategy_stretch custom_strategy_long_term_ma_len custom_strategy_short_term_ma_len custom_strategy_adx_len custom_strategy_atr_len custom_strategy_symbol                
0.5                     200                              20                                6                       3                       SOL-USDT                   -0.815029  
                                                         30                                6                       3                       SOL-USDT                   -0.815029  
                                                         40                                6                       3                       SOL-USDT                   -0.815029  
                        100                              20                                6                       3                       SOL-USDT                   -0.819085  
                                                         30                                6                       3                       SOL-USDT                   -0.819085  
                                                         40                                6                       3                       SOL-USDT                   -0.819085  
                        200                              20                                5                       3                       SOL-USDT                   -0.827408  
                                                      

In [104]:
trades = pf.trades.records_readable
trades
# combined_df = df.join(trades.set_index('Entry Timestamp'), how='outer')  # Join on index
# combined_df


Exit Trade Id                          Column      Size  \
0                 0  (0.5, 100, 20, 5, 3, SOL-USDT)  6.502254   
1                 1  (0.5, 100, 20, 5, 3, SOL-USDT)  7.022075   
2                 2  (0.5, 100, 20, 5, 3, SOL-USDT)  7.212493   
3                 3  (0.5, 100, 20, 5, 3, SOL-USDT)  7.089256   
4                 4  (0.5, 100, 20, 5, 3, SOL-USDT)  4.338113   
...             ...                             ...       ...   
1669           1669  (0.5, 200, 40, 6, 3, SOL-USDT)  0.460594   
1670           1670  (0.5, 200, 40, 6, 3, SOL-USDT)  0.407796   
1671           1671  (0.5, 200, 40, 6, 3, SOL-USDT)  0.386581   
1672           1672  (0.5, 200, 40, 6, 3, SOL-USDT)  0.384850   
1673           1673  (0.5, 200, 40, 6, 3, SOL-USDT)  0.414055   

               Entry Timestamp  Avg Entry Price  Entry Fees  \
0    2021-08-21 08:00:00+00:00        76.819588    0.499500   
1    2021-08-24 16:00:00+00:00        69.674192    0.489257   
2    2021-08-25 08:00:00+00:00        69.256705    0.499514   
3    2021-08-26 04:00:00+00:00        68.626100    0.486508   
4    2021-08-31 16:00:00+00:00       109.501971    0.475032   
...                        ...              ...         ...   
1669 2025-01-07 12:00:00+00:00       211.618227    0.097470   
1670 2025-01-21 00:00:00+00:00       233.681457    0.095294   
1671 2025-01-23 00:00:00+00:00       249.972859    0.096635   
1672 2025-01-25 00:00:00+00:00       248.877342    0.095780   
1673 2025-01-27 04:00:00+00:00       228.936736    0.094792   

                Exit Timestamp  Avg Exit Price  Exit Fees        PnL  \
0    2021-08-22 08:00:00+00:00       75.394908   0.490237 -10.253369   
1    2021-08-24 20:00:00+00:00       71.277160   0.500514  10.266389   
2    2021-08-25 12:00:00+00:00       67.588552   0.487482 -13.018541   
3    2021-08-26 12:00:00+00:00       67.141448   0.475983 -11.487566   
4    2021-09-01 00:00:00+00:00      108.018530   0.468597  -7.378963   
...                        ...             ...        ...        ...   
1669 2025-01-07 16:00:00+00:00      207.308552   0.095485  -2.177966   
1670 2025-01-21 04:00:00+00:00      237.443162   0.096828   1.341885   
1671 2025-01-23 04:00:00+00:00      248.258488   0.095972  -0.855351   
1672 2025-01-25 08:00:00+00:00      246.803404   0.094982  -0.988917   
1673 2025-01-27 08:00:00+00:00      227.059970   0.094015  -0.965892   

        Return Direction  Status  Position Id  
0    -0.020527      Long  Closed            0  
1     0.020984      Long  Closed            1  
2    -0.026062      Long  Closed            2  
3    -0.023612      Long  Closed            3  
4    -0.015534      Long  Closed            4  
...        ...       ...     ...          ...  
1669 -0.022345      Long  Closed         1669  
1670  0.014081      Long  Closed         1670  
1671 -0.008851      Long  Closed         1671  
1672 -0.010325      Long  Closed         1672  
1673 -0.010190      Long  Closed         1673  

[1674 rows x 14 columns]

: 